Import libraries

In [149]:
from bs4 import BeautifulSoup
import requests
import time
import random
import pickle
import shutil
import os

Create lists with edibility symbols

In [2]:
elements = ['🟢!','🟢','🟡🟢','🟡','🔴','🔴☠']

edible = ['🟢!','🟢']
non_edible = ['🟡🟢','🟡']
deadly = ['🔴','🔴☠']

Create 2 lists:
* mushroom names (in format 'Amanita_echinocephala')
* mushroom webpages (in format 'https://grzyby.pl/pelna/gatunki/Amanita_echinocephala')

In [3]:
# Credentials to use full page functionality
credentials = dict(l.rstrip().split('=') for l in open('config.properties') if not l.startswith("#"))
URL_init = "https://www.grzyby.pl/logowanie"

# Log in using credential
form_data = credentials
s = requests.Session()
server = s.post(URL_init, data = form_data)

# Get full list of species
URL = 'https://www.grzyby.pl/pelna/gatunki/'
page = s.get(URL)
soup = BeautifulSoup(page.content, "html.parser")

mushroom_names = []
mushroom_webs = []
for item in soup.find_all('td'):
    if item.find('a', href = True) and '_' in str(item) and '-' not in str(item):
        name = item.find('a').text
        name_clean = item.find('a').text.replace('.htm', '')
        if len(name_clean.split('_')) == 2:
            mushroom_webs.append('https://grzyby.pl/pelna/gatunki/'+name)
            mushroom_names.append(name_clean)

In [4]:
# Check
print(len(mushroom_names))
print(len(mushroom_webs))

4909
4909


Function to create mushroom dictionary

In [71]:
# name - name of dictionary
# l_names - list with mushroom names
# l_webs - list with mushroom websites

def mushroom_dict_init(l_names:list, l_webs:list, name:str=''):
    try:
        mushroom_dict = {l_names[i]: {'edible': None, 'web': l_webs[i], 'img' : []} for i in range(len(l_names))}

        if name != '':
            mushroom_dict['dict_name'] = (f'mushroom_dict_{name}')
        else:
            mushroom_dict['dict_name'] = (f'mushroom_dict')

        print(f'Created {mushroom_dict["dict_name"]} with {len(mushroom_dict)} elements.')
        return mushroom_dict

    except Exception as e:
        print(f'ERROR - not possible to create dictionary: {e}.')

Short dictionary for further tests

In [75]:
# name - name of dictionary
# l_names - list with mushroom names
# l_webs - list with mushroom websites
# l_mushs - list with expected families to be included in final dictionary

def mushroom_dict_short_init(l_names:list, l_webs:list, l_mushs:list, name:str=''):
    l_names_short = []
    l_webs_short = []

    try:
        for mushroom_name in l_names:
            for el in l_mushs:
                if el in mushroom_name:
                    l_names_short.append(mushroom_name)

        for mushroom_web in l_webs:
            for el in l_mushs:
                if el in mushroom_web:
                    l_webs_short.append(mushroom_web)

        mushroom_dict_short = {l_names_short[i]: {'edible': None, 'web': l_webs_short[i], 'img' : []} for i in range(len(l_names_short))}

        if name != '':
            mushroom_dict_short['dict_name'] = (f'mushroom_dict_short_{name}')
        else:
            mushroom_dict_short['dict_name'] = (f'mushroom_dict_short')

        print(f'Created {mushroom_dict_short["dict_name"]} with {len(mushroom_dict_short)} elements.')
        return mushroom_dict_short

    except Exception as e:
        print(f'ERROR - not possible to create dictionary: {e}.')

In [116]:
short_list = ['Agrocybe']

In [120]:
mushroom_dict_short_agrocybe_clean = mushroom_dict_short_init(mushroom_names,mushroom_webs,short_list,'agrocybe_clean')
mushroom_dict_short_agrocybe_copy = mushroom_dict_short_init(mushroom_names,mushroom_webs,short_list,'agrocybe_copy')

Created mushroom_dict_short_agrocybe_clean with 12 elements.
Created mushroom_dict_short_agrocybe_copy with 12 elements.


In [86]:
mushroom_dict_short_clean = mushroom_dict_short_init(mushroom_names,mushroom_webs,short_list,'clean')
mushroom_dict_short_copy = mushroom_dict_short_init(mushroom_names,mushroom_webs,short_list,'copy')

Created mushroom_dict_short_clean with 63 elements.
Created mushroom_dict_short_copy with 63 elements.


In [85]:
# t - short/long sleep time
# dict_1 - dictionary to clean
# dict_2 - copy of dict_1

def dict_edibility_cleanup(dict1:dict, dict2:dict, t = 'long'):
    elements = ['🟢!','🟢','🟡🟢','🟡','🔴','🔴☠']

    edible = ['🟢!','🟢']
    edible_cnt = 0
    non_edible = ['🟡🟢','🟡']
    non_edible_cnt = 0
    deadly = ['🔴','🔴☠']
    deadly_cnt = 0

    dictionary_name = dict1['dict_name']

    try:
        for key, value in dict2.items():
            if key != 'dict_name':
                URL = value['web']
                page = ''

                while page == '':
                    try:
                        page = requests.get(URL)
                        break
                    except:
                        if t == 'long':
                            x = 7
                        else:
                            x = 5

                        print('Connection refused by the server.')
                        print(f'{x} sec break.')
                        time.sleep(x)
                        print('Continue...')
                        continue

                soup = BeautifulSoup(page.content, "html.parser")

                try:
                    if t == 'long':
                        y = random.randint(5,15)
                    else:
                        y = random.randint(3,7)

                    print(f'Starting with {key} ({list(dict2.keys()).index(key)+1}/{len(dict2)}).')
                    edibility = soup.find('div', {'id' : 'tytul-blok'}).find('a').get_text().split()[0]

                    if edibility not in elements:
                        del dict1[key]
                        print(f'>>>>>{key} removed. Mushrooms in clean dictionary: {len(dict1)}/{len(dict2)}. Break for {y} sec.')

                    else:
                        dict1[key]['edible'] = edibility

                        if edibility in edible:
                            edible_cnt += 1
                        if edibility in non_edible:
                            non_edible_cnt += 1
                        if edibility in deadly:
                            deadly_cnt += 1

                        print(f'>>>>>Edibility {edibility} added for: {key}. Break for {y} sec.')

                    time.sleep(y)

                except Exception as e1:
                    if t == 'long':
                        z = random.randint(5,15)
                    else:
                        z = random.randint(3,7)

                    print(f'Error:{str(e1)}. Break for {z} sec.')
                    time.sleep(z)
            else:
                continue

        with open(f'{dictionary_name}.pkl', 'wb') as fp:
            pickle.dump(dict1, fp)

        print('*************************')
        print(f'Clean up done! Dictionary saved as {dictionary_name}.')
        print(f'Mushrooms in clean dictionary: {len(dict1)}')
        print(f'Edible mushrooms: {edible_cnt}')
        print(f'Non-edible mushrooms: {non_edible_cnt}')
        print(f'Deadly mushrooms: {deadly_cnt}')
        print('*************************')

    except Exception as e2:
        print(f'Error:{str(e2)}.')

In [87]:
dict_edibility_cleanup(mushroom_dict_short_clean,mushroom_dict_short_copy,'short')

Starting with Amanita_argentea (1/63).
>>>>>Amanita_argentea removed. Mushrooms in clean dictionary: 62/63. Break for 7 sec.
Starting with Amanita_battarae (2/63).
>>>>>Edibility 🟢 added for: Amanita_battarae. Break for 6 sec.
Starting with Amanita_caesarea (3/63).
>>>>>Edibility 🟢! added for: Amanita_caesarea. Break for 7 sec.
Starting with Amanita_ceciliae (4/63).
>>>>>Amanita_ceciliae removed. Mushrooms in clean dictionary: 61/63. Break for 7 sec.
Starting with Amanita_citrina (5/63).
>>>>>Edibility 🔴 added for: Amanita_citrina. Break for 3 sec.
Starting with Amanita_crocea (6/63).
>>>>>Edibility 🟢 added for: Amanita_crocea. Break for 7 sec.
Starting with Amanita_eliae (7/63).
>>>>>Edibility 🔴 added for: Amanita_eliae. Break for 4 sec.
Starting with Amanita_flavescens (8/63).
>>>>>Amanita_flavescens removed. Mushrooms in clean dictionary: 60/63. Break for 5 sec.
Starting with Amanita_franchetii (9/63).
>>>>>Edibility 🔴 added for: Amanita_franchetii. Break for 4 sec.
Starting with Am

In [121]:
dict_edibility_cleanup(mushroom_dict_short_agrocybe_clean,mushroom_dict_short_agrocybe_copy,'short')

Starting with Agrocybe_arvalis (1/12).
>>>>>Agrocybe_arvalis removed. Mushrooms in clean dictionary: 11/12. Break for 4 sec.
Starting with Agrocybe_cylindracea (2/12).
>>>>>Edibility 🟢 added for: Agrocybe_cylindracea. Break for 7 sec.
Starting with Agrocybe_dura (3/12).
>>>>>Edibility 🟡🟢 added for: Agrocybe_dura. Break for 5 sec.
Starting with Agrocybe_elatella (4/12).
>>>>>Agrocybe_elatella removed. Mushrooms in clean dictionary: 10/12. Break for 4 sec.
Starting with Agrocybe_erebia (5/12).
>>>>>Edibility 🟡 added for: Agrocybe_erebia. Break for 5 sec.
Starting with Agrocybe_firma (6/12).
>>>>>Agrocybe_firma removed. Mushrooms in clean dictionary: 9/12. Break for 5 sec.
Starting with Agrocybe_pediades (7/12).
>>>>>Agrocybe_pediades removed. Mushrooms in clean dictionary: 8/12. Break for 7 sec.
Starting with Agrocybe_praecox (8/12).
>>>>>Edibility 🟢 added for: Agrocybe_praecox. Break for 6 sec.
Starting with Agrocybe_pusiola (9/12).
>>>>>Agrocybe_pusiola removed. Mushrooms in clean dict

In [79]:
# with open('mushroom_dict_clean.pkl', 'rb') as fp:
#     mushroom_dict_clean = pickle.load(fp)

In [ ]:
with open('mushroom_dict_short_clean.pkl', 'rb') as fp:
    mushroom_dict_short = pickle.load(fp)

In [81]:
len(mushroom_dict_short)

676

In [ ]:
mushroom_dict_short_agrocybe_clean

In [112]:
def photo_search(dict1:dict, t = 'long'):
    photos_cnt = 0
    dictionary_name = f'{dict1["dict_name"]}_photos'

    # Credentials
    credentials = dict(l.rstrip().split('=') for l in open('config.properties') if not l.startswith("#"))
    URL_init = "https://www.grzyby.pl/logowanie"

    # Log in using credential
    form_data = credentials
    s = requests.Session()
    server = s.post(URL_init, data = form_data)

    try:
        for key, value in dict1.items():
            if key != 'dict_name':

                URL = value['web']
                page = ''

                while page == '':
                    try:
                        page = s.get(URL)
                        break
                    except:
                        if t == 'long':
                            x = 10
                        else:
                            x = 5

                        print('Connection refused by the server.')
                        print(f'{x} sec break.')
                        time.sleep(x)
                        print('Continue...')
                        continue

                soup = BeautifulSoup(page.content, "html.parser")
                latin_name = ' '.join(soup.find('title').text.split(' ')[0:2])

                try:
                    if t == 'long':
                        y = random.randint(5,17)
                    else:
                        y = random.randint(3,7)

                    print(f'Starting with {key} ({list(dict1.keys()).index(key)+1}/{len(dict1)}).')

                    for item in soup.find_all('img'):

                        try:
                            if 'alt' in item.attrs and latin_name in str(item['alt']) and 'mapa' not in str(item['src']) and 'icon' not in str(item['src']):
                            #if latin_name in str(item['alt']) and 'mapa' not in str(item['src']) and 'icon' not in str(item['src']):
                                value['img'].append(('https://www.grzyby.pl'+item['src']))
                                v = random.randint(1,5)
                                print(f'>>>>>>>>>>Photo found! Break for {v} sec.')
                                time.sleep(v)

                        except Exception as e3:
                            print(f"Error on level 3 for {item}: {e3}.")

                        # if latin_name in str(item['alt']) and 'mapa' not in str(item['src']) and 'icon' not in str(item['src']):
                        #     value['img'].append(('https://www.grzyby.pl'+item['src']))
                        #     v = random.randint(1,5)
                        #     print(f'>>>>>>>>>>Photo found! Break for {v} sec.')
                        #     time.sleep(v)

                    photos_cnt += len(dict1[key]['img'])
                    print(f">>>>>{len(dict1[key]['img'])} photos found. Break for {y} sec.")
                    time.sleep(y)

                except Exception as e2:
                    if t == 'long':
                        z = random.randint(5,17)
                    else:
                        z = random.randint(3,7)

                    print(f'Error on level 2: {e2}. Break for {z} sec.')
                    time.sleep(z)

            else:
                continue

        with open(f'{dictionary_name}.pkl', 'wb') as fp:
            pickle.dump(dict1, fp)

        print('*************************')
        print(f'{photos_cnt} photos found!')
        print(f'Dictionary saved as {dictionary_name}.pkl.')
        print('*************************')

    except Exception as e1:
        print(f'Error on level 1:{e1}.')

In [113]:
with open('mushroom_dict_short_clean.pkl', 'rb') as fp:
    mushroom_dict_short_clean = pickle.load(fp)

In [114]:
photo_search(mushroom_dict_short_clean)

Starting with Amanita_battarae (1/48).
>>>>>>>>>>Photo found! Break for 2 sec.
>>>>>>>>>>Photo found! Break for 3 sec.
>>>>>>>>>>Photo found! Break for 1 sec.
>>>>>>>>>>Photo found! Break for 1 sec.
>>>>>>>>>>Photo found! Break for 1 sec.
>>>>>>>>>>Photo found! Break for 2 sec.
>>>>>>>>>>Photo found! Break for 3 sec.
>>>>>>>>>>Photo found! Break for 5 sec.
>>>>>>>>>>Photo found! Break for 5 sec.
>>>>>>>>>>Photo found! Break for 5 sec.
>>>>>>>>>>Photo found! Break for 1 sec.
>>>>>>>>>>Photo found! Break for 1 sec.
>>>>>>>>>>Photo found! Break for 4 sec.
>>>>>>>>>>Photo found! Break for 3 sec.
>>>>>>>>>>Photo found! Break for 3 sec.
>>>>>15 photos found. Break for 15 sec.
Starting with Amanita_caesarea (2/48).
>>>>>0 photos found. Break for 12 sec.
Starting with Amanita_citrina (3/48).
>>>>>>>>>>Photo found! Break for 4 sec.
>>>>>>>>>>Photo found! Break for 1 sec.
>>>>>>>>>>Photo found! Break for 2 sec.
>>>>>>>>>>Photo found! Break for 4 sec.
>>>>>>>>>>Photo found! Break for 5 sec.
>>>>>

In [122]:
photo_search(mushroom_dict_short_agrocybe_clean)

Starting with Agrocybe_cylindracea (1/5).
>>>>>0 photos found. Break for 11 sec.
Starting with Agrocybe_dura (2/5).
>>>>>>>>>>Photo found! Break for 1 sec.
>>>>>>>>>>Photo found! Break for 2 sec.
>>>>>>>>>>Photo found! Break for 5 sec.
>>>>>>>>>>Photo found! Break for 3 sec.
>>>>>>>>>>Photo found! Break for 3 sec.
>>>>>>>>>>Photo found! Break for 3 sec.
>>>>>>>>>>Photo found! Break for 2 sec.
>>>>>>>>>>Photo found! Break for 2 sec.
>>>>>>>>>>Photo found! Break for 1 sec.
>>>>>>>>>>Photo found! Break for 4 sec.
>>>>>>>>>>Photo found! Break for 4 sec.
>>>>>11 photos found. Break for 17 sec.
Starting with Agrocybe_erebia (3/5).
>>>>>>>>>>Photo found! Break for 4 sec.
>>>>>>>>>>Photo found! Break for 3 sec.
>>>>>>>>>>Photo found! Break for 4 sec.
>>>>>>>>>>Photo found! Break for 3 sec.
>>>>>>>>>>Photo found! Break for 1 sec.
>>>>>>>>>>Photo found! Break for 2 sec.
>>>>>>>>>>Photo found! Break for 5 sec.
>>>>>>>>>>Photo found! Break for 2 sec.
>>>>>>>>>>Photo found! Break for 1 sec.
>>>>>>>

In [ ]:
def photo_download(dict1:dict, t = 'long'):
    # Credentials
    credentials = dict(l.rstrip().split('=') for l in open('config.properties') if not l.startswith("#"))
    URL_init = "https://www.grzyby.pl/logowanie"

    # Log in using credential
    form_data = credentials
    s = requests.Session()
    server = s.post(URL_init, data = form_data)

    try:
        for key, value in dict1.items():
            if key != 'dict_name':

                URL = value['web']
                page = ''

                while page == '':
                    try:
                        page = s.get(URL)
                        break
                    except:
                        if t == 'long':
                            x = 10
                        else:
                            x = 5

                        print('Connection refused by the server.')
                        print(f'{x} sec break.')
                        time.sleep(x)
                        print('Continue...')
                        continue

                soup = BeautifulSoup(page.content, "html.parser")
                latin_name = ' '.join(soup.find('title').text.split(' ')[0:2])

                try:
                    if t == 'long':
                        y = random.randint(5,17)
                    else:
                        y = random.randint(3,7)

                    print(f'Starting with {key} ({list(dict1.keys()).index(key)+1}/{len(dict1)}).')

                    for item in soup.find_all('img'):

                        try:
                            if 'alt' in item.attrs and latin_name in str(item['alt']) and 'mapa' not in str(item['src']) and 'icon' not in str(item['src']):
                            #if latin_name in str(item['alt']) and 'mapa' not in str(item['src']) and 'icon' not in str(item['src']):
                                value['img'].append(('https://www.grzyby.pl'+item['src']))
                                v = random.randint(1,5)
                                print(f'>>>>>>>>>>Photo found! Break for {v} sec.')
                                time.sleep(v)

                        except Exception as e3:
                            print(f"Error on level 3 for {item}: {e3}.")

                        # if latin_name in str(item['alt']) and 'mapa' not in str(item['src']) and 'icon' not in str(item['src']):
                        #     value['img'].append(('https://www.grzyby.pl'+item['src']))
                        #     v = random.randint(1,5)
                        #     print(f'>>>>>>>>>>Photo found! Break for {v} sec.')
                        #     time.sleep(v)

                    photos_cnt += len(dict1[key]['img'])
                    print(f">>>>>{len(dict1[key]['img'])} photos found. Break for {y} sec.")
                    time.sleep(y)

                except Exception as e2:
                    if t == 'long':
                        z = random.randint(5,17)
                    else:
                        z = random.randint(3,7)

                    print(f'Error on level 2: {e2}. Break for {z} sec.')
                    time.sleep(z)

            else:
                continue

        with open(f'{dictionary_name}.pkl', 'wb') as fp:
            pickle.dump(dict1, fp)

        print('*************************')
        print(f'{photos_cnt} photos found!')
        print(f'Dictionary saved as {dictionary_name}.pkl.')
        print('*************************')

    except Exception as e1:
        print(f'Error on level 1:{e1}.')

In [ ]:
photo_download(mushroom_dict_short_agrocybe_clean)

Starting with Agrocybe_cylindracea (1/5).
>>>>>Downloaded 0 pictures. Break 8 sec.
Starting with Agrocybe_dura (2/5).


In [205]:
def photo_download(dict:dict,t = 'long'):
    total_photo_cnt = 0
    folders_cnt = 0

    for key1, value1 in dict.items():
        if key1 != 'dict_name':
            photo_cnt = 0
            print(f'Starting with {key1} ({list(dict.keys()).index(key1)+1}/{len(dict)}).')

            if t == 'long':
                y = random.randint(3,11)
            else:
                y = random.randint(1,5)

            for key2, value2 in value1.items():
                if key2 == 'img':
                    for web in value2:

                        folder_name = str(key1).split("_")[0].lower()

                        if not os.path.exists(folder_name):
                            os.makedirs(folder_name)

                        path = f'{os.getcwd()}\{folder_name}'
                        filename = f'{path}\{key1}_{(value2.index(web)+1):03d}.jpg'
                        folders_cnt += 1

                        URL = web
                        page = ''

                        while page == '':
                            try:
                                page = requests.get(URL, stream = True)
                                break

                            except:
                                if t == 'long':
                                    x = 10
                                else:
                                    x = 5

                                print('Connection refused by the server.')
                                print(f'{x} sec break.')
                                time.sleep(x)
                                print('Continue...')
                                continue

                        if page.status_code == 200:
                            page.raw.decode_content = True

                            with open(filename,'wb') as f:
                                shutil.copyfileobj(page.raw, f)
                                photo_cnt += 1

                        else:
                            print('Image couldn\'t be retreived.')

                    total_photo_cnt += photo_cnt
                    print(f'>>>>>Downloaded {photo_cnt} pictures. Break {y} sec.')
                    time.sleep(y)

    print('*************************')
    print(f'Job done!')
    print(f'Total pictures downloaded: {total_photo_cnt}.')
    print(f'Folders created: {folders_cnt}.')
    print('*************************')

In [198]:
total_photo_cnt = 0

for key1, value1 in mushroom_dict_short_agrocybe_clean.items():
    if key1 != 'dict_name':
        photo_cnt = 0
        print(f'Starting with {key1}.')

        for key2, value2 in value1.items():
            if key2 == 'img':
                for item in value2:
                    folder_name = str(key1).split("_")[0].lower()
                    if not os.path.exists(folder_name):
                        os.makedirs(folder_name)

                    path = f'{os.getcwd()}\{folder_name}'
                    filename = f'{path}\{key1}_{(value2.index(item)+1):03d}.jpg'
                    URL = item
                    page = ''
                    x=10

                    while page == '':
                        try:
                            page = requests.get(URL, stream = True)
                            break
                        except:
                            print('Connection refused by the server.')
                            print(f'{x} sec break.')
                            time.sleep(x)
                            print('Continue...')
                            continue

                    if page.status_code == 200:
                        page.raw.decode_content = True

                        with open(filename,'wb') as f:
                            shutil.copyfileobj(page.raw, f)
                            photo_cnt += 1

                    else:
                        print('Image couldn\'t be retreived.')

                total_photo_cnt += photo_cnt
                print(f'>>>>>Downloaded {photo_cnt} pictures. Break {x} sec.')

print('*************************')
print(f'Job done!')
print(f'Total pictures downloaded: {total_photo_cnt}.')
print('*************************')

Starting with Agrocybe_cylindracea.
>>>>>Downloaded 0 pictures. Break 10 sec.
Starting with Agrocybe_dura.
>>>>>Downloaded 11 pictures. Break 10 sec.
Starting with Agrocybe_erebia.
>>>>>Downloaded 26 pictures. Break 10 sec.
Starting with Agrocybe_praecox.
>>>>>Downloaded 7 pictures. Break 10 sec.
*************************
Job done!
Total pictures downloaded: 44.
*************************


Scratchbook

In [ ]:
for key,value in mushroom_dict_short_agrocybe_clean.items():
    if key != 'dict_name':
        for key2, value2 in value.items():
            if key2 == 'img':
                for item in value2:
                    print(f'File name: {key}_{(value2.index(item)+1):03d}')
                    print(item)

In [186]:
for key1, value in mushroom_dict_short_agrocybe_clean.items():
    if key1 != 'dict_name':
        for key2, value2 in value.items():
            if key2 == 'img':
                for item in value2:
                    print(f'{os.getcwd()}\{str(key1).split("_")[0].lower()}')


C:\Users\User\OneDrive\Edu\Deep Learning\deep_mushroom\agrocybe
C:\Users\User\OneDrive\Edu\Deep Learning\deep_mushroom\agrocybe
C:\Users\User\OneDrive\Edu\Deep Learning\deep_mushroom\agrocybe
C:\Users\User\OneDrive\Edu\Deep Learning\deep_mushroom\agrocybe
C:\Users\User\OneDrive\Edu\Deep Learning\deep_mushroom\agrocybe
C:\Users\User\OneDrive\Edu\Deep Learning\deep_mushroom\agrocybe
C:\Users\User\OneDrive\Edu\Deep Learning\deep_mushroom\agrocybe
C:\Users\User\OneDrive\Edu\Deep Learning\deep_mushroom\agrocybe
C:\Users\User\OneDrive\Edu\Deep Learning\deep_mushroom\agrocybe
C:\Users\User\OneDrive\Edu\Deep Learning\deep_mushroom\agrocybe
C:\Users\User\OneDrive\Edu\Deep Learning\deep_mushroom\agrocybe
C:\Users\User\OneDrive\Edu\Deep Learning\deep_mushroom\agrocybe
C:\Users\User\OneDrive\Edu\Deep Learning\deep_mushroom\agrocybe
C:\Users\User\OneDrive\Edu\Deep Learning\deep_mushroom\agrocybe
C:\Users\User\OneDrive\Edu\Deep Learning\deep_mushroom\agrocybe
C:\Users\User\OneDrive\Edu\Deep Learning

In [ ]:
for item in os.listdir():
    print(f'{os.getcwd()}\{item}')

In [168]:
# remove items w/o edibility from dictionary

for key, value in mushroom_dict_short_copy.items():
    URL = value['web']
    page = ''

    while page == '':
        try:
            page = requests.get(URL)
            break
        except:
            print('Connection refused by the server.')
            print(f'{x} sec break.')
            time.sleep(x)
            print('Continue...')
            continue

    soup = BeautifulSoup(page.content, "html.parser")

    try:
        print(f'Starting with {key} ({list(mushroom_dict_short_copy.keys()).index(key)+1}/{len(mushroom_dict_short_copy)}).')
        edibility = soup.find('div', {'id' : 'tytul-blok'}).find('a').get_text().split()[0]

        if edibility not in elements:
            del mushroom_dict_short_clean[key]
            print(f'{key} removed. Mushrooms left:{len(mushroom_dict_short_clean)}/{len(mushroom_dict_short_copy)}.')

        else:
            mushroom_dict_short_clean[key]['edible'] = edibility
            print(f'Edibility added for:{key}.')

        time.sleep(random.randint(1,5))


    except Exception as e1:
        print(f'Error:{str(e1)}.')
        time.sleep(random.randint(1,5))

Starting with Amanita_argentea (0/127).
Error:'Amanita_argentea'.
Starting with Amanita_battarae (1/127).
Edibility added for:Amanita_battarae.
Starting with Amanita_caesarea (2/127).
Edibility added for:Amanita_caesarea.
Starting with Amanita_ceciliae (3/127).
Error:'Amanita_ceciliae'.
Starting with Amanita_citrina (4/127).
Edibility added for:Amanita_citrina.


KeyboardInterrupt: 

In [58]:
with open('mushroom_dict_clean.pkl', 'wb') as fp:
    pickle.dump(mushroom_dict_clean, fp)
    print('Dictionary saved successfully to file.')

Dictionary saved successfully to file.


In [26]:
# Remove elements with non-described edibility - SHORT
for key, value in mushroom_dict_amanita_clean_copy.items():
    URL = value['web']
    page = requests.get(URL, timeout = 5)
    soup = BeautifulSoup(page.content, "html.parser")

    latin_name = ' '.join(soup.find('title').text.split(' ')[0:2])
    edibility = soup.find('div', {'id' : 'tytul-blok'}).find('a').get_text().split()[0]

    if edibility not in elements:
        del mushroom_dict_amanita_clean[key]
    else:
        mushroom_dict_amanita_clean[key]['edible'] = edibility

In [ ]:
# Get latin name from website
# >> sometimes there is mismatch between page name and latin name (title), used in alt (alternative text)
URL = "https://www.grzyby.pl/pelna/gatunki/Psilocybe_semilanceata.htm"
page = s.get(URL)
soup = BeautifulSoup(page.content, "html.parser")

latin_name = ' '.join(soup.find('title').text.split(' ')[0:2])

In [34]:
# EDIBLE - AWESOME
# Get edible/poisonous feature from the website
URL = "https://www.grzyby.pl/pelna/gatunki/Boletus_edulis.htm"
page = requests.get(URL)
soup = BeautifulSoup(page.content, "html.parser")

soup.find('div', {'id' : 'tytul-blok'})#.find('a')#.get_text().split()[0]

<div class="w3-display-container w3-padding" id="tytul-blok">
<div class="w3-hide-large w3-hide-medium w3-small w3-display-topleft w3-text-gray" style="margin-left:4px"><b>grzyby.pl</b></div>
<div class="w3-small" style="padding-top:8px"><a href="/oatlasie.htm">O atlasie »</a></div><h1>przeciążenie</h1>
</div>

In [47]:
# DEADLY
# Get edible/poisonous feature from the website
URL = "https://www.grzyby.pl/pelna/gatunki/Amanita_phalloides.htm"
page = s.get(URL)
soup = BeautifulSoup(page.content, "html.parser")

soup.find('div', {'id' : 'tytul-blok'}).find('a').get_text().split()[0]

'🔴☠'

In [48]:
# NON_EDIBLE
# Get edible/poisonous feature from the website
URL = "https://www.grzyby.pl/pelna/gatunki/Hygrophoropsis_aurantiaca.htm"
page = requests.get(URL)
soup = BeautifulSoup(page.content, "html.parser")

soup.find('div', {'id' : 'tytul-blok'}).find('a').get_text().split()[0]

'🟡🟢'

In [49]:
# NON_EDIBLE
# Get edible/poisonous feature from the website
URL = "https://www.grzyby.pl/pelna/gatunki/Tylopilus_felleus.htm"
page = requests.get(URL)
soup = BeautifulSoup(page.content, "html.parser")

soup.find('div', {'id' : 'tytul-blok'}).find('a').get_text().split()[0]

'🟡'

In [40]:
elements = ['🟢!','🟢','🟡🟢','🟡','🔴','🔴☠']

edible = ['🟢!','🟢']
non_edible = ['🟡🟢','🟡']
deadly = ['🔴','🔴☠']

In [ ]:
# Get all images sources from website
# URL = "https://www.grzyby.pl/pelna/gatunki/Psilocybe_semilanceata.htm"
# page = s.get(URL)
# soup = BeautifulSoup(page.content, "html.parser")
#
# for item in soup.find_all('img'):
#     if 'Psilocybe semilanceata' in str(item['alt']) and 'mapa'not in str(item['src']) and 'icon'not in str(item['src']):
#         print('https://www.grzyby.pl'+item['src'])

In [28]:
# # Add images to dictionary - SHORT
# # Credentials
# credentials = dict(l.rstrip().split('=') for l in open('config.properties') if not l.startswith("#"))
# URL_init = "https://www.grzyby.pl/logowanie"
#
# # Log in using credential
# form_data = credentials
# s = requests.Session()
# server = s.post(URL_init, data = form_data)
#
# # Add images to dict
# for key, value in mushroom_dict_amanita_clean.items():
#     URL = value['web']
#     page = s.get(URL, timeout = 3)
#     soup = BeautifulSoup(page.content, "html.parser")
#     latin_name = ' '.join(soup.find('title').text.split(' ')[0:2])
#
#     for item in soup.find_all('img'):
#         if latin_name in str(item['alt']) and 'mapa'not in str(item['src']) and 'icon'not in str(item['src']):
#             value['img'].append(('https://www.grzyby.pl'+item['src']))

In [ ]:
-- https://www.google.com/search?safe=off&site=&tbm=isch&source=hp&q=amanita-muscaria-mushroom&oq=amanita-muscaria-mushroom&gs_l=img

In [286]:
# # Version for full dict (~5000 elements)
# # Find edible/non-edible/poisonous/deadly tags
# elements = []
# for key, value in mushroom_dict.items():
#     URL = value['web']
#     page = requests.get(URL, timeout = 10)
#     soup = BeautifulSoup(page.content, "html.parser")
#
#     try:
#         if (soup.find('div', {'id' : 'tytul-blok'}).find('a').get_text().split()[0]) not in elements:
#             el1 = soup.find('div', {'id' : 'tytul-blok'}).find('a').get_text()
#             el2 = el1.split()
#             el3 = el2[0]
#             elements.append(el3)
#     except:
#         print('error:',get.error())

C:\Users\User\anaconda3\lib\site-packages\urllib3\connectionpool.py:1045: InsecureRequestWarning: Unverified HTTPS request is being made to host 'grzyby.pl'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
C:\Users\User\anaconda3\lib\site-packages\urllib3\connectionpool.py:1045: InsecureRequestWarning: Unverified HTTPS request is being made to host 'www.grzyby.pl'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
C:\Users\User\anaconda3\lib\site-packages\urllib3\connectionpool.py:1045: InsecureRequestWarning: Unverified HTTPS request is being made to host 'grzyby.pl'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
C:\Users\User\anaconda3\lib\site-packages\urllib3\connectionpool.py:1045: I

error


C:\Users\User\anaconda3\lib\site-packages\urllib3\connectionpool.py:1045: InsecureRequestWarning: Unverified HTTPS request is being made to host 'grzyby.pl'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
C:\Users\User\anaconda3\lib\site-packages\urllib3\connectionpool.py:1045: InsecureRequestWarning: Unverified HTTPS request is being made to host 'www.grzyby.pl'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
C:\Users\User\anaconda3\lib\site-packages\urllib3\connectionpool.py:1045: InsecureRequestWarning: Unverified HTTPS request is being made to host 'grzyby.pl'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
C:\Users\User\anaconda3\lib\site-packages\urllib3\connectionpool.py:1045: I

In [217]:
# Add images to dictionary - TEST
# Credentials
credentials = dict(l.rstrip().split('=') for l in open('config.properties') if not l.startswith("#"))
URL_init = "https://www.grzyby.pl/logowanie"

# Log in using credential
form_data = credentials
s = requests.Session()
server = s.post(URL_init, data = form_data)

# Add images to dict
for key, value in mushroom_dict_short.items():
    URL = value['web']
    page = s.get(URL)
    soup = BeautifulSoup(page.content, "html.parser")
    latin_name = ' '.join(soup.find('title').text.split(' ')[0:2])

    for item in soup.find_all('img'):
        if latin_name in str(item['alt']) and 'mapa'not in str(item['src']) and 'icon'not in str(item['src']):
            value['img'].append(('https://www.grzyby.pl'+item['src']))

In [220]:
# Check
for key, value in mushroom_dict_short.items():
    if len(value['img']) != 0:
        print(key)
        print(value['edible'])
        print(value['web'])
        print(value['img'])

Boletopsis_leucomelaena
p
https://grzyby.pl/pelna/gatunki/Boletopsis_leucomelaena.htm
['https://www.grzyby.pl/pelna/foto/GREJ/GREJ-146176-276439ss.jpg', 'https://www.grzyby.pl/pelna/foto/GREJ/GREJ-146176-276440ss.jpg', 'https://www.grzyby.pl/pelna/foto/GREJ/GREJ-146176-276441ss.jpg', 'https://www.grzyby.pl/pelna/foto/GREJ/GREJ-146176-276442ss.jpg', 'https://www.grzyby.pl/pelna/foto/GREJ/GREJ-146176-276443ss.jpg', 'https://www.grzyby.pl/pelna/foto/GREJ/GREJ-184257-402936ss.jpg', 'https://www.grzyby.pl/pelna/foto/GREJ/GREJ-184257-402937ss.jpg', 'https://www.grzyby.pl/pelna/foto/GREJ/GREJ-184257-402938ss.jpg', 'https://www.grzyby.pl/pelna/foto/GREJ/GREJ-184257-402939ss.jpg', 'https://www.grzyby.pl/pelna/foto/GREJ/GREJ-146176-276439ss.jpg', 'https://www.grzyby.pl/pelna/foto/GREJ/GREJ-146176-276440ss.jpg', 'https://www.grzyby.pl/pelna/foto/GREJ/GREJ-146176-276441ss.jpg', 'https://www.grzyby.pl/pelna/foto/GREJ/GREJ-146176-276442ss.jpg', 'https://www.grzyby.pl/pelna/foto/GREJ/GREJ-146176-2764